# CAMISIM
CAMISIM es un `Programa` para simular datos metagenomicos a partir de genomas, a grandes rasgos este programa toma uno o varios archivos de genomas,y por un proceso de corte aleatorio de secuencias crea un archivo de datos metagenomicos.

A continuación muestro los pasos para hacer una recreaccion de este algoritmos, y exploicare cada una delas funciones creadas.

In [1]:
import os
import math
import random
import numpy as np

from pathlib import Path
from random import seed
from random import randint

La primera funcion se encarga unicamente de leer cada archivo (genoma) y convertirlo en un diccionario en donde las 'llaves' son los nombres de cada genoma y los 'valores' la secuencia de nucleotidos.

In [8]:
# funcion para lectura de archivos
# ingresa un archivo multifasta y arroja una lista con cada secuencia (contig)
dic = {}
def lectura_genoma(File):
    lista = []
    with open(File,'r') as f:
        lines=f.read() # lectura decada linea del archivo
        lines=lines.split('>') # identificador de '>'
        lines=['>'+ x for x in lines[1:]] # lista con cada elemento que comienza con '>'
        for x in lines:
            #file_name=x.split('\n')[0][1:] # quita los saltos de linea reemplazandolos con '\n'
            #fil=open(file_name+'.fa','w')
            #fil.write(x)
            #fil.close()
            x2 = x.replace("\n",",",1) # el primer '\n' se reemplazapor una coma
            x3 = x2.replace("\n","") # los siguientes se quitan
            lista.append(x3) # lista con un contig en cada elemento y su identificador

        
        
        # LONGITUDES ¿¿¿???
        # convertir la lista en un diccionario        
        for x in lista:
            x = x.split(',')
            dic[x[0]] = x[1] 
        return(dic)    

In [9]:
lectura_genoma('/home/csilva/GIT/Tesis_Maestria/Data/new-c-genomes/Clavibacter_michiganensis_subsp_capsici_1101.fna-cortado.fna')

{'>NZ_CP048049.1': '...',
 '>NZ_CP048050.1': '...'}

Esta segunda funcion se encarga de cortar una secuencia de nucleotidos dada, a partir de una pocision y una longitud dada.

In [10]:
# funcion para cortar reads, dado una pocision de inicio y una longitud de corte
def cutout(read,i,n_length): 
    cropped_read = read[i:i+n_length]
    return(cropped_read) 

In [12]:
cutout(dic['>NZ_CP048049.1'],5, 10)

'CGACCGCTCC'

Ahora, la ultima funcion se compone delafuncion anterior para cortar reads, y se complementa, haciendo esto para cada genoma dentro de diccionario creado.

In [15]:
# funcion para cortar los reads aleatoriamente
# Al ingresar un conjunto de genomas, este nos arroja un metagenoma con varios reads tomados de los genomas iniciales
# para esto se le entrega el numero de reads deseados por cada genoma y la longitud.
def reads(diccionario,longitud,num_reads):  # num_reads
    dic2 = {}
    contig = 0
    k = 0
    
    # LONGITUD Y NUM_READS DEPENDERA DE LAS LONGITUDES DE LOS CONTIG
    # LA LONGITUD 
    
    #LAS LONGITUDES DEPENDEN DE LA CALIDAD
    
    
    while k < num_reads:
        for key in diccionario:#range(len(diccionario.keys())):
            newkey = key + '_' + str(k) 
            contig = random.choice(list(diccionario.values())) # escoje un contig al azar 
            i = randint(1,(len(contig)-longitud)) # toma una pocision de inicio al azar
            dic2[newkey] = cutout(contig,i,longitud) # para el contig dado anteriormente, se corta desde la pocision i de lonjitud ln
            # se debe calcular cuantas veces va a escoger cada contig,dependiendo del tamaño del contig inicial      
        k += 1
    return(dic2)

In [23]:
# funcion de creacion archivo .fastq
    
def crea_fastq(diccionario,longitud,file_name):
    file = open(file_name,'wt')
    for key in diccionario: 
        file.write(str(key))
        file.write(str('\n'))
        file.write(str(diccionario[key]))
        file.write(str('\n'))
        file.write(str('+'))
        file.write(str('\n'))
        file.write(str('A'*longitud)) #calidad
        file.write(str('\n'))     
    file.close()


In [18]:
dicreads=reads(dic,10,3)
dicreads

{'>NZ_CP048049.1_0': 'TTGATCTCGT',
 '>NZ_CP048050.1_0': 'CCTCTCAGCC',
 '>NZ_CP048049.1_1': 'CCGCTCCTGC',
 '>NZ_CP048050.1_1': 'GTAGAAGGCC',
 '>NZ_CP048049.1_2': 'CCCTGACCGC',
 '>NZ_CP048050.1_2': 'GGCTTGCGGG'}

In [24]:
crea_fastq(dicreads,10,"prueba2.fastq")

A continuación se quiere agrupar todo dentro de una clase, para poder llamar a la clase completa cuando sea necesario, y poder realizar el proceso para varios archivos al mismo tiempo. Empezando con un solo archivo como prueba de la clase.

Esta clase se compone de tres funciones, las cuales:
 * Lee uno o varios archivos .fasta los cuales contienen genomas con uno o varios contigs.
 * Corta un read (secuencia genomica) de un tamaño dado y desde una posición aleatoria dada.
 * Crea un diccionario de reads de varios metagenomicos.

In [ ]:
class CAMISIM_CAMI1:
    def __init__(self):
        self.dic = {}
        self.list = []
        
    # funcion para lectura de archivos
    # ingresa un archivo multifasta y arroja una lista con cada secuencia (contig)
    dic = {}
    def lectura_genoma(File):
        lista = []
        with open(File,'r') as f: #with open(ruta + '/' + File,'r') as f:
            lines=f.read() # lectura decada linea del archivo
            lines=lines.split('>') # identificador de '>'
            lines=['>'+ x for x in lines[1:]] # lista con cada elemento que comienza con '>'
            for x in lines:
                x2 = x.replace("\n",",",1) # el primer '\n' se reemplazapor una coma
                x3 = x2.replace("\n","") # los siguientes se quitan
                lista.append(x3) # lista con un contig en cada elemento y su identificador
            # convertir la lista en un diccionario        
            for x in lista:
                x = x.split(',')
                dic[x[0]] = x[1] 
            return(dic)  
    
    # funcion para cortar reads, dado una pocision de inicio y una longitud de corte
    def cutout(read,i,n_length): 
        cropped_read = read[i:i+n_length]
        return(cropped_read) 
    
    # funcion para cortar los reads aleatoriamente
    # Al ingresar un conjunto de genomas, este nos arroja un metagenoma con varios reads tomados de los genomas iniciales
    # para esto se le entrega el numero de reads deseados por cada genoma y la longitud.
    def reads(diccionario,longitud,num_reads):  # num_reads
        dic2 = {}
        contig = 0
        k = 0
        while k < num_reads:
            for key in diccionario:#range(len(diccionario.keys())):
                newkey = key + '_' + str(k) 
                contig = random.choice(list(diccionario.values())) # escoje un contig al azar 
                i = randint(1,(len(contig)-longitud)) # toma una pocision de inicio al azar
                dic2[newkey] = cutout(contig,i,longitud) # para el contig dado anteriormente, se corta desde la pocision i de lonjitud ln
                # se debe calcular cuantas veces va a escoger cada contig,dependiendo del tamaño del contig inicial      
            k += 1
        return(dic2)
    
    # funcion de creacion archivo .fastq, tomandoel diccionario de reads cortados y la calidad de los reads
    def crea_fastq(diccionario,longitud,file_name):
        file = open(file_name,'wt')
        for key in diccionario: 
            file.write(str(key))
            file.write(str('\n'))
            file.write(str(diccionario[key]))
            file.write(str('\n'))
            file.write(str('+'))
            file.write(str('\n'))
            file.write(str('A'*longitud)) #calidad
            file.write(str('\n'))     
        file.close()
    

In [ ]:
CAMISIM_CAMI1.reads(dic,5,10) 

Y por ultimo realizandole unas pocas modificaciones a la clase, para poder realizar el proceso para varios archivos de genomas.

y aplicando lo visto en clase sobre lectura de arhivos, e iteracion sobre cada uno de ellos.

In [ ]:
# 

In [6]:
# Funcion para la lectura de los nombres de los todos los archivos de genomas
# toma la ruta de la carpeta donde estan los genomas, y crea un listado de los nombres de los archivos
# para poder realizar la lectura de los mismos.
ruta = '/home/csilva/GIT/Tesis_Maestria/Data/new-c-genomes'
contenido = os.listdir(ruta)
genomes = []
for i in contenido:
    if os.path.isfile(os.path.join(ruta,i)) and i.endswith('.fna'):
        genomes.append(i)
n = len(genomes) # número de genomas (número de archivos)
diccionario_reads_metagenoma = {}
    

{'>NZ_CP086346.1_0': 'ACGGCGCAGCCCGCGGTGGCGGCGTCGGCGTCGGACGCGCGCAGGACCGGCGCATGATCCGGCGCGCCCACGCCGTCCCGCTGCGTCGGCGTCTGCGCGGCGGGGGCGAGGAGGCGGTCGTCGAGGAGGCGGAGGAGATCGCCGCGTTCG', '>NZ_CP086347.1_0': 'GAGCGTGGAGTACGAGCGCGCGGTCGCCCTGCTCGGCTACACGCACGCGGCGCTGCTCGACGAGGTCATCGACGCGGTCGCTGGGCACGACGCGGCCGCCGCGTTCGCGGGGGTCGACCGGGTCATCCAGACCGGCCAGGATCCGCGCCG', '>NZ_CP048049.1_0': 'CCGCGACATCCGCGCCCTCGCCCGCGACGGCCGGATCATGGTCATCGGCGCCCAGAGCGGCGCGCCCACGAGCATCGCGCTCGGCCAGCTGATGGCTCGGCGAGGGCGGATCTGGGGCACGACGCTCCGCGCCCGGGACGCCGACGACAA', '>NZ_CP048050.1_0': 'CGGGGCTCGGCCTCGCGGACGCCATCGACCTCACCGACGGCCCGCTCGCGCGCCGCGGCGACGACATGGTCTGGACGGGCGTGATCGACGAGGTCGTGTTCGAGCTCCGCTACCCGGCGGAGAGCGGGGATCCCGTCGGCGACGAGCACT', '>NZ_CP048047.1_0': 'CTCACCGACTCGACGACGCAGCGCAACGTCGGCGTCGCGCTCGGCCATTCGCTGCTGGCGCTCGACAACGTCGGGCGCGGGCTCCTCGAGATCGACGTCGACCGGGCGCTGCTCGCGGCCGACCTCGACGCGAACTGGGAGATCCTCGGC', '>NZ_CP048048.1_0': 'GCAAGTTCGAGGGTCCCGTCGTCGCCGAGCGCGAGCACGTCGTGCGCAGCGCGATGAAGGTGCCCGTGCACACGGCCATCGAGGTCGACCCGATGGGCCAGGGCACGC

In [27]:
genomes

['Clavibacter_michiganensis_subsp_nebraskensis_44.fna-cortado.fna',
 'Clavibacter_michiganensis_subsp_capsici_1101.fna-cortado.fna',
 'Clavibacter_michiganensis_subsp_capsici_1106.fna-cortado.fna',
 'Clavibacter_michiganensis_subsp_insidiosus_CFBP_1195.fna-cortado.fna']

In [ ]:
# Con esta funcion queremos llamar a las funciones de la clase,para todos los archivos en la lista 'genomes'
for i,x in enumerate(genomes):
    